In [1]:
from Evaluation.find_ranking_citation import CitationRanking
from sklearn.metrics.pairwise import linear_kernel,cosine_similarity
from Evaluation.write_result import WriteResult
from data_loading_ginny import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from  Evaluation.eval_Ginny import Metrics
from Rec_configuraiton import Rec_configuration 
#from reranking.re_ranking_title import ReRankingTitle
#advanced deep learning stuff
import torch
#from bert_serving.client import BertClient
import pickle
from collections import defaultdict
import numpy as np
import scipy
from sentence_transformers import SentenceTransformer
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
import os 

/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/

In [ ]:
class Master:
    def __init__(self, rerank = True):
        self.rec_conf = Rec_configuration()
        self.article_title, self.article_abstract, self.geo_title, \
        self.geo_summary, self.citation_data = DataLoading().get_all_details() #we should get actual citations
        self.auto_rank = CitationRanking(self.citation_data)
        self.write_res = WriteResult()
     
        '''
        #later we're gonna test on all datasets that has referenced paper 
        self.geo_test_data = ["GSE20361", "GSE23137", "GSE1640", "GSE41034", "GSE1864", "GSE44700", "GSE50988"]#, \
                              #"GSE46045", "GSE32869", "GSE22955", "GSE41072", "GSE50624", "GSE18684", "GSE770", \
                              #"GSE9048", "GSE9854", "GSE23135", "GSE23136", "GSE23139", "GSE49583", "GSE49584", \
                              #"GSE49586", "GSE64073", "GSE38623", "GSE3113", "GSE41491", "GSE29641", "GSE26002", \
                              #"GSE17018", "GSE71121", "GSE21618", "GSE23138", "GSE20988", "GSE52710", "GSE14103", \
                              #"GSE53294"] #36
        '''
        #or,
        choose = list(self.citation_data.keys())
        self.geo_test_data = [key for key in choose if self.citation_data[key] != []] #76,064
        #self.rr = ReRankingTitle() # i definitely need to work on this as well (re-ranking title using bert)
        self.top_threshold = 10 #sounds nice
        self.rerank = rerank
        #bert related
        self.model_bert = SentenceTransformer('bert-base-nli-mean-tokens')
        self.model_addr = self.rec_conf.model_path_bert #subject to change
        self.res_addr = self.rec_conf.result_address_bert #subject to change

        
    def re_rank_bert(self, geo_sim_dict, article_title, geo_title, pmid_ls): #pmid_ls. should be the complete pmid: similarity score column dimension
        assert np.asarray(list(geo_sim_dict.values())).shape[1] == len(pmid_ls) #the # of columns should be equal to total # of pmids
        geo_words = list(geo_title.values())#a list of words? I don't need to split for bert
        title_words = list(article_title.values())
        sim_value = linear_kernel(self.model_bert.encode(geo_words), self.model_bert.encode(title_words))
        for i, geo_id in enumerate(geo_sim_dict): #key of the dictionary is the geo-ids
            #for each geo_id, adding re-ranking values
            geo_sim_dict[geo_id] += sim_value[i, :]
        return self.sorting(geo_sim_dict, pmid_ls)
    
    def sorting(self, geo_sim_dict, pmid_ls):
          
        '''
        for each geo_id, give a list of recommendations 
        this could be for non-reranking or reranking
        '''
        similarity_dict = defaultdict()
        sim_np = np.asarray(list(geo_sim_dict.values()))
        idx_np = np.argsort(-sim_np, axis= 1) #so the big values will be in front 
        #take on # of top_threshold
        idx_np = idx_np[:,:self.top_threshold]
        sim_np_taketop = np.take_along_axis(sim_np, idx_np, axis=1) 
        for i, geo_id in enumerate(geo_sim_dict):
            pmid_selected = list(np.take(pmid_ls, idx_np[i]))
            selected = dict(zip(pmid_selected, sim_np_taketop[i]))
            similarity_dict[geo_id] = selected     
        return similarity_dict
    
    def process(self):
        #check paths and check vecs        
        pmids, bert_vecs = None, None #this should be loading something

        # This is for loading the pre-trained bert models.
        if bert_vecs is not None and pmids is not None:
            print('load trained models and encoded publications vectors')
            '''
            
            '''
        else:
            print('Building models')
            joined_dict_article = {}
            for pmid in self.article_title: #for articles, encoding the articles
                #print('pmid')
                #print(pmid)
                if (self.article_title[pmid] + self.article_abstract[pmid]).strip() != '':
                    joined_dict_article[pmid] = self.article_title[pmid] + ' ' + self.article_abstract[pmid]
            #should be some training here, otherwise just do the easiest encodinh
            pmids, bert_vecs = list(joined_dict_article.keys()), self.model_bert.encode(list(joined_dict_article.values()))
            with open(self.res_addr + 'base/bert_vecs', 'wb') as handle:
                pickle.dump(bert_vecs, handle, protocol=pickle.HIGHEST_PROTOCOL)
            with open(self.res_addr + 'base/pmids', 'wb') as handle:
                pickle.dump(pmids, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
        #keep only articles with non-zero values
        #new_article_abstract = {new_key: self.article_abstract[new_key] for new_key in pmids} #770,525
        #new_article_title = {new_key: self.article_title[new_key] for new_key in pmids}
   
    
        joined_dict_geo = {} # maxium: 76,064
        # screening first for those geo_ids with pmids 
        for geo_id in self.geo_test_data:
            print('geo_id')
            print(geo_id)
            if (self.geo_title[geo_id] + self.geo_summary[geo_id]).strip() != '':
                #only get the ones with actual texts
                joined_dict_geo[geo_id] = self.geo_title[geo_id] + ' ' + self.geo_summary[geo_id]
        geo_ids, geo_bert_vecs = list(joined_dict_geo.keys()), self.model_bert.encode(list(joined_dict_geo.values()))
        with open(self.res_addr + 'base/geo_bert_vecs', 'wb') as handle:
            pickle.dump(geo_bert_vecs, handle, protocol=pickle.HIGHEST_PROTOCOL)
        with open(self.res_addr + 'base/geo_ids', 'wb') as handle:
            pickle.dump(geo_ids, handle, protocol=pickle.HIGHEST_PROTOCOL)        
        
        #with open(self.res_addr + 'parrot.pkl', 'wb') as f:
            #pickle.dump(mylist, f)
        #keep only geo datasets with non-zero values
        #new_geo_summary = {new_key: self.geo_summary[new_key] for new_key in geo_ids} #770,525
        #new_geo_title = {new_key: self.geo_title[new_key] for new_key in geo_ids}
        
        """
        similarity_value_dict = defaultdict()
        similarity_scores = linear_kernel(geo_bert_vecs, bert_vecs)
        #we need to export this value
        np.save(self.res_addr + 'base/similarity_scores', similarity_scores)
        #load this later
        #np.load(self.res_addr + 'base/similarity_scores')
        print(similarity_scores.shape)
        #call the re-ranking or not 
        for i, geo_id in enumerate(geo_ids): #this is only from testing geo_id
            print(geo_id)
            #print(geo_id)
            similarity_value_dict[geo_id] =  list(similarity_scores[i])
            #similarity_value_dict[geo_id] = scipy.spatial.distance.cdist([geo_bert_vecs[i]], bert_vecs, "cosine")[0]
        if self.rerank:
            new_similarity_dict = self.re_rank_bert(geo_sim_dict = similarity_value_dict,
                                                       article_title = new_article_title,
                                                       geo_title = new_geo_title, 
                                                       pmid_ls = pmids)
        else:
            new_similarity_dict =  self.sorting(geo_sim_dict = similarity_value_dict, pmid_ls = pmids)
        
        with open(self.res_addr + 'base/new_similarity_dict.pickle', 'wb') as handle:
            pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
        
        #screen for geo_ids that actually has citations t
        for id, geo_id in enumerate(geo_ids): 
            #this has already stored in a pickled list of geo_haspmid.pickle
            temp_selected = new_similarity_dict[geo_id]
            #modify this later based on rerank or base; plain or futher trained
            if self.rerank:
                self.write_res.write(self.res_addr + 'rerank/'  + geo_id + '.txt', temp_selected)
            else:
                #we will have things here this time. 
                self.write_res.write(self.res_addr + 'base/'  + geo_id + '.txt', temp_selected)
            self.auto_rank.find_citations(geo_id, list(temp_selected.keys())) #keys are a list of pmids
            
        a, b, c, d = self.auto_rank.get_values() #need to modify this 
        print('good geo recommendations = {}, top1 hit geo recommendations = {}, bad geo recommendations = {}, '
              'geo without citations = {}'.format(a, b, c, d))
        #we need many more than just MRR
        #MRR 
        print('MRR')
        print(Metrics(self.citation_data).calculate_mrr(new_similarity_dict)) #mrr
        #recall @1 and recall @10
        print('recall@1, recall@10')
        print(Metrics(self.citation_data).calculate_recall_at_k(similarity_dict, 1))
        print(Metrics(self.citation_data).calculate_recall_at_k(similarity_dict, 10))
        #Precision@1 and precision10
        print('precision@1, precision@10')
        print(Metrics(self.citation_data).calculate_precision_at_k(similarity_dict, 1))        
        print(Metrics(self.citation_data).calculate_precision_at_k(similarity_dict, 10))
        #MAP@10
        print(Metrics(self.citation_data).calculate_calculate_MAP_at_k(similarity_dict))
        """

In [ ]:
def main():
    x = Master(rerank = False)
    x.process()


if __name__ == '__main__':
    main()

In [2]:
#read-in stored vec 
res_addr = 'results/bert_plain/base/'
res_addr2 = 'results/bert_plain/'
with open(res_addr +'bert_vecs', 'rb') as fp:
      bert_vecs = pickle.load(fp)
with open(res_addr +'geo_bert_vecs', 'rb') as fp:
      geo_bert_vecs = pickle.load(fp)        
        
with open(res_addr +'pmids', 'rb') as fp:
      pmids = pickle.load(fp)
with open(res_addr +'geo_ids', 'rb') as fp:
      geo_ids = pickle.load(fp)      
        
        
bert_vecs = torch.tensor(np.array(bert_vecs)).cuda()
#pmids = torch.tensor(pmids).cuda()


geo_bert_vecs = torch.tensor(np.array(geo_bert_vecs))
#geo_ids = torch.tensor(geo_ids)

In [ ]:
'''
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
targets = le.fit_transform(['cat','dog', 'more'])
le.classes_
#array([1, 2, 6])
le.transform(['cat','dog', 'more'])
#array([0, 0, 1, 2]...)
print(le.inverse_transform([0, 0, 1, 2])
array([1, 1, 2, 6])


'''

In [3]:
print(pmids[:2])
geo_ids[:2]

['25240462', '20122219']


['GSE103837', 'GSE89809']

In [4]:
b_size = 64 #let's try 256 instead of 512???
geo_bert_vecs_data = TensorDataset(geo_bert_vecs)
geo_bert_vecs_sampler = SequentialSampler(geo_bert_vecs_data) #sequential here 
geo_bert_vecs_dataloader = DataLoader(geo_bert_vecs_data, sampler=geo_bert_vecs_sampler, batch_size= 64)

In [5]:
geo_bert_vecs[:2]

tensor([[-0.6874,  0.5635, -0.2512,  ..., -0.5094, -0.1190,  0.8729],
        [ 0.0218,  0.5726,  0.1366,  ...,  0.0139, -0.6200,  0.4939]])

In [6]:
def sort_this(geo_sim_dict, pmid_ls, top_threshold =10):

    '''
    for each geo_id, give a list of recommendations 
    this could be for non-reranking or reranking
    '''
    geo_sim_dict = dict(geo_sim_dict)
    similarity_dict = defaultdict()
    sim_np = np.asarray(list(geo_sim_dict.values()))
    idx_np = np.argsort(-sim_np, axis= 1) #so the big values will be in front 
    #take on # of top_threshold
    idx_np = idx_np[:,:top_threshold]
    sim_np_taketop = np.take_along_axis(sim_np, idx_np, axis=1) 
    for i, geo_id in enumerate(geo_sim_dict):
        print('working')
        pmid_selected = list(np.take(pmid_ls, idx_np[i]))
        selected = dict(zip(pmid_selected, sim_np_taketop[i]))
        similarity_dict[geo_id] = selected     
    return similarity_dict

In [2]:
from Evaluation.find_ranking_citation import CitationRanking
from Evaluation.write_result import WriteResult
from data_loading import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from Evaluation.eval_Ginny import Metrics      
    
    
#self.rec_conf = Rec_configuration()
_, _, _, _, citation_data = DataLoading().get_all_details() #we should get actual citations
auto_rank = CitationRanking(citation_data)
write_res = WriteResult()  

Lemmatization is false, if required turn on again
Loading all geo related preprocessed datasets
Loaded all geo related processed datasets
Loading all title and abstract
Loaded all title and abstract


In [8]:
import os

In [10]:
device  = torch.device("cuda" if torch.cuda.is_available() else "cpu")
for step, batch in enumerate(geo_bert_vecs_dataloader):
    #print(batch)
    batch = batch[0].to(device)
    print(batch.shape)
    geo_ids_batch = geo_ids[step*b_size: (step+1)*b_size]
    #geo_batch, geo_ids_batch = batch
    similarity_value_dict = dict()
    similarity_scores = cosine_similarity(batch.cpu().numpy(), bert_vecs.cpu().numpy())
    #similarity_scores = torch.cdist(batch, bert_vecs)  
    #we need to export this value
    np.save(res_addr2 + 'similarity_scores_batch_' + str(step), similarity_scores)#.cpu().numpy())
    #load this later
    #np.load(self.res_addr + 'base/similarity_scores')
    print(similarity_scores.shape)
    #call the re-ranking or not 
    for i, geo_id in enumerate(geo_ids_batch): #this is only from testing geo_id
        print(geo_id)
        similarity_value_dict[geo_id] =  list(similarity_scores[i])#.cpu().numpy())
        #similarity_value_dict[geo_id] = scipy.spatial.distance.cdist([geo_bert_vecs[i]], bert_vecs, "cosine")[0]
        '''
        if self.rerank:
        new_similarity_dict = self.re_rank_bert(geo_sim_dict = similarity_value_dict,
                                                   article_title = new_article_title,
                                                   geo_title = new_geo_title, 
                                                   pmid_ls = pmids)
        '''

    new_similarity_dict =  sort_this(geo_sim_dict = similarity_value_dict, pmid_ls = pmids)
    new_similarity_dict = dict(new_similarity_dict)
    filename =  res_addr2 + 'new_similarity_dict_batch_' + str(step)
    os.makedirs(os.path.dirname(filename), exist_ok=True)
    with open(res_addr2 + 'new_similarity_dict_batch_' + str(step), 'wb') as handle:
        pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
    print('export dict')
     
        #screen for geo_ids that actually has citations t
    for id, geo_id in enumerate(geo_ids_batch): 
        print(geo_id)
        #this has already stored in a pickled list of geo_haspmid.pickle
        temp_selected = new_similarity_dict[geo_id]
        filename =  res_addr2 + geo_id + '.txt'
        os.makedirs(os.path.dirname(filename), exist_ok=True)
        write_res.write(res_addr2  + geo_id + '.txt', temp_selected)
        auto_rank.find_citations(geo_id, list(temp_selected.keys())) #keys are a list of pmids

a, b, c, d = auto_rank.get_values() #need to modify this 
print('good geo recommendations = {}, top1 hit geo recommendations = {}, bad geo recommendations = {}, '
      'geo without citations = {}'.format(a, b, c, d))
#we need many more than just MRR

torch.Size([64, 768])
(64, 770525)
GSE103837
GSE89809
GSE11663
GSE55127
GSE61914
GSE96174
GSE108140
GSE55064
GSE77553
GSE836
GSE48997
GSE4248
GSE71695
GSE16495
GSE92231
GSE36779
GSE28180
GSE93962
GSE97290
GSE76313
GSE27104
GSE78579
GSE33842
GSE96211
GSE92438
GSE27139
GSE25518
GSE72425
GSE96905
GSE8547
GSE12256
GSE76217
GSE43669
GSE10903
GSE102695
GSE105628
GSE72212
GSE44657
GSE92332
GSE81888
GSE4500
GSE83148
GSE32214
GSE70328
GSE81569
GSE55869
GSE65781
GSE37546
GSE89581
GSE101478
GSE1862
GSE43906
GSE24450
GSE3574
GSE1865
GSE101823
GSE32925
GSE84727
GSE62309
GSE70285
GSE64244
GSE83819
GSE35910
GSE61188
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working

(64, 770525)
GSE75427
GSE4807
GSE48344
GSE44714
GSE23122
GSE31007
GSE58456
GSE59651
GSE21181
GSE17389
GSE44356
GSE34510
GSE78738
GSE50803
GSE83435
GSE40738
GSE74446
GSE22962
GSE29617
GSE98976
GSE11133
GSE11347
GSE45430
GSE84122
GSE66178
GSE39375
GSE79901
GSE21120
GSE58318
GSE229
GSE59071
GSE88426
GSE78633
GSE52662
GSE66966
GSE94069
GSE25842
GSE89944
GSE37450
GSE38916
GSE5174
GSE20214
GSE15434
GSE114205
GSE9482
GSE74925
GSE53621
GSE88414
GSE53017
GSE63926
GSE87153
GSE27911
GSE38596
GSE46262
GSE79108
GSE59246
GSE84822
GSE6022
GSE65352
GSE37047
GSE57590
GSE21607
GSE88997
GSE27632
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working


(64, 770525)
GSE8668
GSE25082
GSE59842
GSE44456
GSE75282
GSE59980
GSE46299
GSE82439
GSE83727
GSE49039
GSE40626
GSE82430
GSE64561
GSE12265
GSE16352
GSE102867
GSE83134
GSE64029
GSE55298
GSE45535
GSE96481
GSE89060
GSE12670
GSE72537
GSE39528
GSE46889
GSE105302
GSE50748
GSE54709
GSE94960
GSE64945
GSE56253
GSE79062
GSE30325
GSE75271
GSE13925
GSE55279
GSE51573
GSE64680
GSE57570
GSE51525
GSE102596
GSE7094
GSE96855
GSE49042
GSE3872
GSE81689
GSE30610
GSE4824
GSE31438
GSE38222
GSE47759
GSE64106
GSE87992
GSE24135
GSE91485
GSE23546
GSE45795
GSE79680
GSE95237
GSE34721
GSE18151
GSE2180
GSE74796
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
worki

(64, 770525)
GSE56701
GSE9277
GSE7998
GSE47188
GSE32978
GSE28636
GSE85807
GSE8030
GSE43541
GSE18125
GSE31902
GSE71503
GSE7103
GSE11365
GSE27077
GSE18967
GSE101199
GSE87972
GSE78152
GSE39597
GSE50065
GSE43982
GSE28521
GSE50607
GSE23031
GSE9894
GSE83483
GSE94538
GSE48019
GSE67721
GSE55795
GSE100942
GSE7030
GSE85866
GSE108846
GSE34026
GSE112829
GSE72186
GSE108625
GSE23113
GSE77135
GSE33750
GSE59609
GSE23261
GSE28509
GSE44551
GSE112763
GSE77558
GSE85681
GSE65076
GSE95012
GSE91952
GSE43114
GSE60221
GSE10702
GSE23887
GSE72071
GSE2684
GSE50591
GSE106017
GSE77778
GSE55501
GSE21717
GSE35678
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
wor

(64, 770525)
GSE91602
GSE74805
GSE38158
GSE17167
GSE6811
GSE9278
GSE31214
GSE98351
GSE61111
GSE8017
GSE76575
GSE34281
GSE89462
GSE49314
GSE43412
GSE87611
GSE58841
GSE23381
GSE95473
GSE64695
GSE48472
GSE87471
GSE22267
GSE27111
GSE62107
GSE37417
GSE25206
GSE107676
GSE76468
GSE72364
GSE603
GSE15224
GSE72001
GSE46207
GSE32521
GSE12367
GSE21805
GSE41902
GSE43721
GSE59021
GSE62389
GSE83586
GSE38863
GSE23888
GSE46398
GSE86897
GSE51553
GSE1515
GSE27289
GSE81519
GSE108243
GSE21653
GSE12243
GSE54097
GSE26646
GSE103877
GSE83407
GSE82428
GSE104584
GSE102859
GSE33507
GSE12887
GSE5208
GSE110446
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

...

(64, 770525)
GSE100864
GSE3584
GSE45551
GSE94197
GSE79134
GSE34474
GSE6082
GSE10065
GSE95089
GSE17892
GSE14361
GSE39525
GSE110987
GSE102641
GSE19370
GSE96490
GSE28100
GSE69202
GSE84264
GSE16102
GSE99268
GSE43143
GSE105834
GSE98254
GSE104290
GSE47763
GSE28630
GSE3004
GSE81116
GSE45280
GSE101209
GSE76826
GSE87806
GSE498
GSE59579
GSE87353
GSE78193
GSE90053
GSE77537
GSE32899
GSE88127
GSE105988
GSE46031
GSE72865
GSE57068
GSE58708
GSE72132
GSE20460
GSE59735
GSE84512
GSE71491
GSE42065
GSE84986
GSE46986
GSE35340
GSE46109
GSE68834
GSE7178
GSE89635
GSE105098
GSE95679
GSE13728
GSE98461
GSE16761
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
w

(64, 770525)
GSE46150
GSE69104
GSE65360
GSE42527
GSE49369
GSE90284
GSE738
GSE1463
GSE49049
GSE80397
GSE9982
GSE49513
GSE73700
GSE21918
GSE90251
GSE25196
GSE23226
GSE988
GSE25956
GSE18930
GSE19139
GSE62036
GSE78997
GSE52011
GSE9105
GSE32543
GSE22428
GSE82067
GSE11502
GSE7606
GSE42630
GSE29293
GSE90746
GSE105154
GSE54193
GSE24777
GSE21086
GSE24998
GSE72705
GSE78107
GSE72237
GSE4405
GSE42561
GSE56907
GSE87868
GSE59786
GSE91908
GSE83176
GSE10286
GSE10873
GSE8230
GSE90409
GSE24801
GSE19384
GSE65387
GSE56777
GSE56544
GSE74119
GSE11921
GSE107296
GSE22410
GSE1411
GSE19792
GSE91674
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
work

(64, 770525)
GSE108932
GSE96303
GSE17444
GSE28715
GSE53894
GSE448
GSE81021
GSE34903
GSE59810
GSE62979
GSE17070
GSE96480
GSE107267
GSE111489
GSE65793
GSE75360
GSE59804
GSE97077
GSE15859
GSE14006
GSE22747
GSE12383
GSE28717
GSE97791
GSE57132
GSE66202
GSE84690
GSE33127
GSE9437
GSE36917
GSE59768
GSE47703
GSE64447
GSE7377
GSE25028
GSE90396
GSE29291
GSE40011
GSE5349
GSE44211
GSE92876
GSE89156
GSE88899
GSE91720
GSE961
GSE89076
GSE105986
GSE21522
GSE2156
GSE3622
GSE46204
GSE9977
GSE13000
GSE33335
GSE39411
GSE19206
GSE14391
GSE35418
GSE97102
GSE79875
GSE66463
GSE16684
GSE104203
GSE93980
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working


(64, 770525)
GSE42876
GSE84344
GSE43565
GSE45359
GSE111888
GSE19282
GSE16893
GSE34417
GSE2995
GSE30537
GSE66198
GSE36191
GSE94840
GSE17976
GSE14854
GSE55216
GSE68358
GSE10607
GSE14773
GSE66237
GSE41608
GSE75705
GSE88228
GSE16597
GSE46208
GSE79076
GSE32474
GSE48372
GSE72964
GSE26360
GSE94251
GSE20270
GSE72596
GSE78320
GSE73785
GSE22511
GSE10684
GSE110207
GSE11825
GSE88395
GSE78187
GSE45967
GSE104714
GSE24829
GSE26252
GSE1728
GSE27011
GSE77445
GSE63990
GSE7274
GSE22723
GSE72094
GSE31713
GSE46067
GSE41133
GSE33607
GSE40727
GSE35922
GSE56038
GSE73388
GSE100898
GSE11256
GSE54447
GSE8917
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
wor

(64, 770525)
GSE79860
GSE24276
GSE74912
GSE9317
GSE36065
GSE19447
GSE24849
GSE98067
GSE101206
GSE104657
GSE73557
GSE69711
GSE66984
GSE6045
GSE91617
GSE46902
GSE38768
GSE98031
GSE28113
GSE8710
GSE1766
GSE17919
GSE108199
GSE31049
GSE101754
GSE2430
GSE26086
GSE12989
GSE43144
GSE66050
GSE68630
GSE18005
GSE25609
GSE52644
GSE2689
GSE85834
GSE105255
GSE54065
GSE71397
GSE12834
GSE62193
GSE42568
GSE43808
GSE49418
GSE93229
GSE27295
GSE11709
GSE57042
GSE84566
GSE28490
GSE74748
GSE10860
GSE44690
GSE87800
GSE84409
GSE35156
GSE37274
GSE41086
GSE73633
GSE41941
GSE22045
GSE2128
GSE91929
GSE47949
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
working
worki

In [11]:
print(step)

1188


In [11]:
#import glob
#files = glob.glob(res_addr + "similarity_scores_batch_*")
new_similarity_dict =  {}
#print
#for file in files:
for i in range(step +1):
    with open(res_addr2 + "new_similarity_dict_batch_" + str(i), 'rb') as fp:
        dict_batch = pickle.load(fp)
        new_similarity_dict.update(dict_batch)
#dict.update(dict2)
#dict.update(dict3)
with open(res_addr2 + 'new_similarity_dict.pickle', 'wb') as handle:
    pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [4]:
res_addr2 = 'results/bert_plain/base/'
with open(res_addr +'new_similarity_dict.pickle', 'rb') as fp:
      new_similarity_dict = pickle.load(fp)

In [16]:
with open(res_addr + 'new_similarity_dict.pickle', 'wb') as handle:
    pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [19]:
for k, v in new_similarity_dict.items():
    print(k)
    print(v)
    break

GSE103837
{'14739298': 5.3257413, '22521726': 5.4766445, '11776436': 5.560794, '19956200': 5.607554, '16424012': 5.624469, '24411611': 5.6387305, '12560328': 5.6436267, '21649464': 5.6962285, '19799812': 5.7130003, '17506945': 5.720672}


In [ ]:
#let's try to see the results if they are better or worse 

In [5]:
#MRR 
print('MRR:')
print(Metrics(citation_data).calculate_mrr(new_similarity_dict)) #mrr
#recall @1 and recall @10
print('recall@1, recall@10:')
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 1))
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 10))
#Precision@1 and precision10
print('precision@1, precision@10:')
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 1))        
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 10))
#MAP@10
print(Metrics(citation_data).calculate_MAP_at_k(new_similarity_dict))

MRR:
0.37227028873489293
recall@1, recall@10:
0.348727063327426
0.40640337862281506
precision@1, precision@10:
0.35456306411506916
0.041454300669038754
0.37203555493625695


In [ ]:
dict = {'e':1, 'd':2}
for i, d in enumerate(dict):
    print(i,d)

In [ ]:
import numpy as np
rs = np.array([[0, 0, 0], [0, 1, 0], [1, 0, 0]])
    
r = np.asarray(rs)[:,:3]


In [ ]:
r.shape[0]

In [ ]:
def precision_at_k(r, k):
    """Score is precision @ k
    Relevance is binary (nonzero is relevant).
    >>> r = [0, 0, 1]
    >>> precision_at_k(r, 1)
    0.0
    >>> precision_at_k(r, 2)
    0.0
    >>> precision_at_k(r, 3)
    0.33333333333333331
    >>> precision_at_k(r, 4)
    Traceback (most recent call last):
        File "<stdin>", line 1, in ?
    ValueError: Relevance score length < k
    Args:
        r: Relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Precision @ k
    Raises:
        ValueError: len(r) must be >= k
    """
    assert k >= 1
    r = np.asarray(r)[:k] != 0
    if r.size != k:
        raise ValueError('Relevance score length < k')
    return np.mean(r)

In [ ]:
def average_precision( r):
    """Score is average precision (area under PR curve)
    Relevance is binary (nonzero is relevant).
    >>> r = [1, 1, 0, 1, 0, 1, 0, 0, 0, 1]
    >>> delta_r = 1. / sum(r)
    >>> sum([sum(r[:x + 1]) / (x + 1.) * delta_r for x, y in enumerate(r) if y])
    0.7833333333333333
    >>> average_precision(r)
    0.78333333333333333
    Args:
        r: Relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Average precision
    """
    r = np.asarray(r) != 0
    out = [precision_at_k(r, k+1) for k in range(r.size) if r[k]]
    if not out:
        return 0.
    return np.mean(out)


def mean_average_precision(rs):
    """Score is mean average precision
    Relevance is binary (nonzero is relevant).
    >>> rs = [[1, 1, 0, 1, 0, 1, 0, 0, 0, 1]]
    >>> mean_average_precision(rs)
    0.78333333333333333
    >>> rs = [[1, 1, 0, 1, 0, 1, 0, 0, 0, 1], [0]]
    >>> mean_average_precision(rs)
    0.39166666666666666
    Args:
        rs: Iterator of relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Mean average precision
    """
    return np.mean([average_precision(r) for r in rs])

In [ ]:
rs =[[1,0,1,0,0,1,0,0,1,1],[0,1,0,0,1,0,1,0,0,0]]
mean_average_precision(rs)

In [ ]:
!pip install ml_metrics

In [ ]:
import ml_metrics as metrics
metrics.mapk(actual =[[1,1,1,1,1,0,0,0,0,0],[1,1,1,0,0,0,0,0,0,0]],predicted = [[1,0,1,0,0,1,0,0,1,1],[0,1,0,0,1,0,1,0,0,0]], k=10)

In [ ]:
#semantic match problem:
embedder = SentenceTransformer('bert-base-nli-mean-tokens')

# Corpus with example sentences
corpus = ['A man is eating a food.',
          'A man is eating a piece of bread.',
          'The girl is carrying a baby.',
          'A man is riding a horse.',
          'A woman is playing violin.',
          'Two men pushed carts through the woods.',
          'A man is riding a white horse on an enclosed ground.',
          'A monkey is playing drums.',
          'A cheetah is running behind its prey.']

corpus_embeddings = embedder.encode(corpus)



In [ ]:
queries = ['A man is eating pasta.', 
           'Someone in a gorilla costume is playing a set of drums.', 
           'A cheetah chases prey on across a field.']
query_embeddings = embedder.encode(queries)


In [ ]:
for query, query_embedding in zip(queries, query_embeddings):
    distances = scipy.spatial.distance.cdist([query_embedding], corpus_embeddings, "cosine")[0]
    print(distances)

In [ ]:
distances

In [23]:
from sklearn.metrics.pairwise import cosine_similarity 

In [24]:
import torch.nn.functional as F
input1 = torch.Tensor([[2,3]])
input2 = torch.Tensor([[2,3],[4,5]])
output = cosine_similarity(input1,input2)
print(output)

[[1.0000001 0.9962406]]
